## Import Statement

In [1]:
import pandas as pd

### read the data

In [2]:
df = pd.read_csv("../all_port_labelled.csv")

In [3]:
df.head(2)

Unnamed: 0  Index  Unnamed: 0.1  \
0         0.0    8.0          34.0   
1         1.0   10.0          63.0   

                                            Headline  \
0  Grasberg Mine- Grasberg mine workers extend st...   
1  Indonesia: Undersea internet cables damaged by...   

                                             Details  Severity  \
0  Media sources indicate that workers at the Gra...  Moderate   
1  News sources are stating that recent typhoons ...     Minor   

              Category     Region       Datetime    Year  ...   IT   EP  NEW  \
0  Mine Workers Strike  Indonesia  28/5/17 17:08  2017.0  ...  0.0  0.0  0.0   
1       Travel Warning  Indonesia   4/9/17 14:30  2017.0  ...  0.0  0.0  0.0   

   CSD  RPE   MN   NM if_labeled  Month  Week  
0  0.0  0.0  0.0  1.0      False    5.0  21.0  
1  0.0  0.0  1.0  0.0      False    4.0  14.0  

[2 rows x 46 columns]

### Clean empty data

In [4]:
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import string

# nltk.download('punkt')
# nltk.download('stopwords')
# nltk.download('wordnet')


def clean_text(text):
    # Lowercase
    text = text.lower()
    # Tokenization
    tokens = word_tokenize(text)
    # Removing punctuation
    tokens = [word for word in tokens if word not in string.punctuation]
    # Removing stop words
    stop_words = set(stopwords.words("english"))
    tokens = [word for word in tokens if word not in stop_words]
    # Lemmatization
    lemmatizer = WordNetLemmatizer()
    tokens = [lemmatizer.lemmatize(word) for word in tokens]

    return " ".join(tokens)

In [5]:
import nltk

nltk.download("omw-1.4")

[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\ellay\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


True

### The Details column has an issue

some of the data are of the type float and none of the text processing functions can be applied to it therefore we have to process it

In [6]:
text_df = df[["Details", "maritime_label"]]
text_df.info()
text_df["Details_cleaned"] = text_df["Details"].apply(
    lambda x: clean_text(x) if not isinstance(x, float) else None
)
# no_nan_df[no_nan_df["Details"].apply(lambda x: print(type(x)))]
# cleaned_df = text_df[text_df["Details"].apply(lambda x: clean_text(x))]
# cleaned_df = df['Details'][1:2]
# type(no_nan_df["Details"][0])
# print(clean_text(no_nan_df["Details"][0]))
text_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5782 entries, 0 to 5781
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   Details         5781 non-null   object
 1   maritime_label  5781 non-null   object
dtypes: object(2)
memory usage: 90.5+ KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5782 entries, 0 to 5781
Data columns (total 3 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Details          5781 non-null   object
 1   maritime_label   5781 non-null   object
 2   Details_cleaned  5781 non-null   object
dtypes: object(3)
memory usage: 135.6+ KB


<ipython-input-6-254c36cdfdd3>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  text_df['Details_cleaned'] = text_df['Details'].apply(lambda x: clean_text(x) if not isinstance(x, float) else None)


In [7]:
processed_data = text_df.dropna()
processed_data.head()

Details maritime_label  \
0  Media sources indicate that workers at the Gra...          FALSE   
1  News sources are stating that recent typhoons ...          FALSE   
2  The persisting port congestion at Shanghai’s Y...           TRUE   
3  Updated local media sources from Jakarta indic...           TRUE   
4  According to local police in Jakarta, two expl...           TRUE   

                                     Details_cleaned  
0  medium source indicate worker grasberg mine ex...  
1  news source stating recent typhoon impact hong...  
2  persisting port congestion shanghai ’ yangshan...  
3  updated local medium source jakarta indicate e...  
4  according local police jakarta two explosion c...

## Naive Bayes Model

In [8]:
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer

# from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, classification_report

In [9]:
X = processed_data["Details_cleaned"]
y = processed_data["maritime_label"]

In [10]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

In [11]:
# vectorizer = CountVectorizer()
# X_train_vec = vectorizer.fit_transform(X_train)
# X_test_vec = vectorizer.transform(X_test)

tfidf_vectorizer = TfidfVectorizer(max_features=1000)
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)
X_test_tfidf = tfidf_vectorizer.transform(X_test)

In [12]:
naive_bayes = MultinomialNB()
naive_bayes.fit(X_train_tfidf, y_train)

MultinomialNB()

In [13]:
predictions = naive_bayes.predict(X_test_tfidf)

In [14]:
accuracy = accuracy_score(y_test, predictions)
print("Accuracy of Naive Bayes model:", accuracy)
print(classification_report(y_test, predictions))

Accuracy of Naive Bayes model: 0.8582541054451167
              precision    recall  f1-score   support

       FALSE       0.88      0.94      0.91       847
        TRUE       0.79      0.65      0.71       310

    accuracy                           0.86      1157
   macro avg       0.83      0.79      0.81      1157
weighted avg       0.85      0.86      0.85      1157



## Logistic Regression model

In [15]:
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

In [16]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

In [17]:
tfidf_vectorizer = TfidfVectorizer(max_features=1000)
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)
X_test_tfidf = tfidf_vectorizer.transform(X_test)

In [18]:
model = LogisticRegression()
model.fit(X_train_tfidf, y_train)

LogisticRegression()

In [19]:
y_pred = model.predict(X_test_tfidf)

accuracy = accuracy_score(y_test, y_pred)
print("Accuracy of Logistic Regression Model:", accuracy)
print(classification_report(y_test, y_pred))

Accuracy of Logistic Regression Model: 0.9317199654278306
              precision    recall  f1-score   support

       FALSE       0.92      0.99      0.96       847
        TRUE       0.98      0.76      0.86       310

    accuracy                           0.93      1157
   macro avg       0.95      0.88      0.91      1157
weighted avg       0.93      0.93      0.93      1157



## Support Vector Machine (SVM) model

In [20]:
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

In [21]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

In [22]:
tfidf_vectorizer = TfidfVectorizer(max_features=1000)
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)
X_test_tfidf = tfidf_vectorizer.transform(X_test)

In [23]:
svm_model = SVC(kernel="linear")
svm_model.fit(X_train_tfidf, y_train)

SVC(kernel='linear')

In [24]:
y_pred = svm_model.predict(X_test_tfidf)

In [25]:
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy of SVM model:", accuracy)
print(classification_report(y_test, y_pred))

Accuracy of SVM model: 0.9498703543647364
              precision    recall  f1-score   support

       FALSE       0.94      1.00      0.97       847
        TRUE       0.99      0.82      0.90       310

    accuracy                           0.95      1157
   macro avg       0.96      0.91      0.93      1157
weighted avg       0.95      0.95      0.95      1157



## Random Forest Model

In [26]:
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

In [27]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

In [28]:
tfidf_vectorizer = TfidfVectorizer(max_features=1000)
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)
X_test_tfidf = tfidf_vectorizer.transform(X_test)

In [29]:
rf_model = RandomForestClassifier(n_estimators=100, random_state=42)
rf_model.fit(X_train_tfidf, y_train)

RandomForestClassifier(random_state=42)

In [30]:
y_pred = rf_model.predict(X_test_tfidf)

In [31]:
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy of Random Forest Model:", accuracy)
print(classification_report(y_test, y_pred))

Accuracy of Random Forest Model: 0.9636992221261884
              precision    recall  f1-score   support

       FALSE       0.96      0.99      0.98       847
        TRUE       0.98      0.88      0.93       310

    accuracy                           0.96      1157
   macro avg       0.97      0.94      0.95      1157
weighted avg       0.96      0.96      0.96      1157



## Simpe Neural Network

In [1]:
pip install tensorflow

  Obtaining dependency information for tensorflow from https://files.pythonhosted.org/packages/f9/14/67e9b2b2379cb530c0412123a674d045eca387dfcfa7db1c0028857b0a66/tensorflow-2.16.1-cp311-cp311-macosx_12_0_arm64.whl.metadata
  Obtaining dependency information for absl-py>=1.0.0 from https://files.pythonhosted.org/packages/a2/ad/e0d3c824784ff121c03cc031f944bc7e139a8f1870ffd2845cc2dd76f6c4/absl_py-2.1.0-py3-none-any.whl.metadata
  Obtaining dependency information for astunparse>=1.6.0 from https://files.pythonhosted.org/packages/2b/03/13dde6512ad7b4557eb792fbcf0c653af6076b81e5941d36ec61f7ce6028/astunparse-1.6.3-py2.py3-none-any.whl.metadata
  Obtaining dependency information for flatbuffers>=23.5.26 from https://files.pythonhosted.org/packages/bf/45/c961e3cb6ddad76b325c163d730562bb6deb1ace5acbed0306f5fbefb90e/flatbuffers-24.3.7-py2.py3-none-any.whl.metadata
  Obtaining dependency information for gast!=0.5.0,!=0.5.1,!=0.5.2,>=0.2.1 from https://files.pythonhosted.org/packages/fa/39/5aae571e

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.0/227.0 MB 3.3 MB/s eta 0:00:0000:0100:02
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 133.7/133.7 kB 2.8 MB/s eta 0:00:00 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 3.5 MB/s eta 0:00:0000:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 3.7 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 2.8 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 26.4/26.4 MB 4.0 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 389.8/389.8 kB 2.4 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.5/65.5 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 394.2/394.2 kB 3.0 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 3.0 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 